In [1]:
import numpy as np

In [2]:
from keras.datasets import mnist

2024-02-28 20:47:43.678182: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-02-28 20:47:44.217528: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-02-28 20:47:44.222094: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-02-28 20:47:45.071979: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [5]:
class FClayer ():
    def __init__(self, input_size, output_size):
              
        self.weights = np.random.rand(input_size, output_size) - 0.5
        self.bias = np.random.rand(1, output_size) - 0.5
    
    def forward_propagation(self, input_data):
        self.input = input_data
        self.output = np.dot(self.input, self.weights) + self.bias
        return self.output
    
    
    def backward_propagation(self, output_error, learning_rate):
        input_error = np.dot(output_error, self.weights.T)
        weight_error = np.dot(self.input.T, output_error)
      
        self.weights -= learning_rate*weight_error
        self.bias -= learning_rate*output_error
        return input_error

In [6]:
class ActivationLayer():

    def __init__(self, activation, activation_prime):
        self.activation = activation
        self.activation_prime = activation_prime
        
      
    def forward_propagation(self, input_data):
        self.input = input_data
        self.output = self.activation(self.input)
        return self.output

    def backward_propagation(self, output_error, learning_rate):
        return self.activation_prime(self.input) * output_error

In [33]:
def tanh(x):
    return np.tanh(x)

def tanh_prime(x):
    return 1-np.tanh(x)**2

In [8]:
def sigmoid(x):
    return 1/(1+ np.exp(-x))

def sigmoid_prime(x):
    s = sigmoid(x)
    return s * (1-s)

In [19]:
def ReLU(x):
    return np.maximum(0, x)

def ReLU_prime(x):
    return np.where(x > 0, 1, 0)

In [36]:
def softmax(x):
    e_x = np.exp(x - np.max(x, axis=-1, keepdims=True))
    return e_x / np.sum(e_x, axis=-1, keepdims=True)

def softmax_prime(x):
    s = softmax(x)
    return s * (1 - s)

In [10]:
def mse(y_pred, y_true):
    return np.mean(np.power(y_pred-y_true, 2))

def mse_prime(y_pred, y_true):
    return 2*(y_pred - y_true)/y_true.size

In [11]:
class Network:

    def __init__(self):
        self.layers = []
        self.loss= None
        self.loss_prime = None

    # Adding layer to the network
    def add(self,layer):
        self.layers.append(layer)
        
    # Set loss to use
    def use(self, loss, loss_prime):
        self.loss= loss
        self.loss_prime = loss_prime

    # Predicting output for the given input
    def predict(self, input_data):
        result = []
        samples = len(input_data)

        # running through all samples
        for i in range (samples):
            output = input_data[i]
            #forward propogation function used
            for layer in self.layers:
                output = layer.forward_propagation(output)
            result.append(output)
         
        return result  

    #training the network
    def fit(self, x_train, y_train, epochs, learning_rate):
        samples = len(x_train)

        #training loop
        for i in range(epochs):
            err = 0
            #forward propogation
            for j in range (samples):
                output = x_train[j]
                for layer in self.layers:
                    output = layer.forward_propagation(output)

                #compute loss
                err += self.loss(y_train[j], output)

                
                #backward propogation
                error = self.loss_prime(y_train[j], output)

                for layer in reversed(self.layers):
                    error = layer.backward_propagation(error, learning_rate)

            # calculate average error on all samples
            err /= samples
            print('epoch %d %d error=%f' %(i+1,epochs,err))
            accuracy = 100-err
            print('accuracy= %f' %(accuracy))

In [12]:
# training data

x_train = np.array([[[0,0]],[[0,1]],[[1,0]],[[1,1]]])
y_train = np.array([[[1]],[[0]],[[0]],[[1]]])

# building network

net = Network()
net.add(FClayer(2,3))
net.add(ActivationLayer(tanh, tanh_prime))
net.add(FClayer(3,1))
net.add(ActivationLayer(tanh, tanh_prime))

# training the model

net.use(mse, mse_prime)
net.fit(x_train, y_train, epochs=1000, learning_rate=0.05)

#test

out = net.predict(x_train)
print(out)

epoch 1 1000 error=0.348168
accuracy= 99.651832
epoch 2 1000 error=0.598232
accuracy= 99.401768
epoch 3 1000 error=1.116882
accuracy= 98.883118
epoch 4 1000 error=1.658351
accuracy= 98.341649
epoch 5 1000 error=1.987776
accuracy= 98.012224
epoch 6 1000 error=2.159227
accuracy= 97.840773
epoch 7 1000 error=2.253601
accuracy= 97.746399
epoch 8 1000 error=2.310608
accuracy= 97.689392
epoch 9 1000 error=2.347886
accuracy= 97.652114
epoch 10 1000 error=2.373812
accuracy= 97.626188
epoch 11 1000 error=2.392722
accuracy= 97.607278
epoch 12 1000 error=2.407041
accuracy= 97.592959
epoch 13 1000 error=2.418211
accuracy= 97.581789
epoch 14 1000 error=2.427140
accuracy= 97.572860
epoch 15 1000 error=2.434423
accuracy= 97.565577
epoch 16 1000 error=2.440465
accuracy= 97.559535
epoch 17 1000 error=2.445550
accuracy= 97.554450
epoch 18 1000 error=2.449883
accuracy= 97.550117
epoch 19 1000 error=2.453615
accuracy= 97.546385
epoch 20 1000 error=2.456860
accuracy= 97.543140
epoch 21 1000 error=2.459706


In [13]:
(x_train,y_train),(x_test,y_test) = mnist.load_data()

In [15]:
x_train = x_train.reshape(x_train.shape[0], 1, 28*28)
x_train = x_train.astype('float32')
x_train /= 255

x_test = x_test.reshape(x_test.shape[0], 1, 28*28)
x_test = x_test.astype('float32')
x_test /= 255

In [16]:
net = Network()
net.add(FClayer(28*28, 100))                
net.add(ActivationLayer(sigmoid, sigmoid_prime))
net.add(FClayer(100, 50))                   
net.add(ActivationLayer(sigmoid, sigmoid_prime))
net.add(FClayer(50, 10))                    
net.add(ActivationLayer(sigmoid, sigmoid_prime))

In [32]:
net.use(mse, mse_prime)
net.fit(x_train[0:1000], y_train[0:1000], epochs= 35, learning_rate=0.05)

# test on 3 samples
out = net.predict(x_test)
print("\n")
print("predicted values : ")
print(out[0:3], end="\n")
print("true values : ")
print(y_test[0:3])

epoch 1 35 error=28.114000
accuracy= 71.886000
epoch 2 35 error=28.114000
accuracy= 71.886000
epoch 3 35 error=28.114000
accuracy= 71.886000
epoch 4 35 error=28.114000
accuracy= 71.886000
epoch 5 35 error=28.114000
accuracy= 71.886000
epoch 6 35 error=28.114000
accuracy= 71.886000
epoch 7 35 error=28.114000
accuracy= 71.886000
epoch 8 35 error=28.114000
accuracy= 71.886000
epoch 9 35 error=28.114000
accuracy= 71.886000
epoch 10 35 error=28.114000
accuracy= 71.886000
epoch 11 35 error=28.114000
accuracy= 71.886000
epoch 12 35 error=28.114000
accuracy= 71.886000
epoch 13 35 error=28.114000
accuracy= 71.886000
epoch 14 35 error=28.114000
accuracy= 71.886000
epoch 15 35 error=28.114000
accuracy= 71.886000
epoch 16 35 error=28.114000
accuracy= 71.886000
epoch 17 35 error=28.114000
accuracy= 71.886000
epoch 18 35 error=28.114000
accuracy= 71.886000
epoch 19 35 error=28.114000
accuracy= 71.886000
epoch 20 35 error=28.114000
accuracy= 71.886000
epoch 21 35 error=28.114000
accuracy= 71.886000
e

In [30]:
net = Network()
net.add(FClayer(28*28, 32))                
net.add(ActivationLayer(ReLU, ReLU_prime))
net.add(FClayer(32, 15))                   
net.add(ActivationLayer(ReLU, ReLU_prime))
net.add(FClayer(15, 10))                    
net.add(ActivationLayer(ReLU, ReLU_prime))

In [31]:
net.use(mse, mse_prime)
net.fit(x_train[0:2000], y_train[0:2000], epochs= 35, learning_rate=0.05)

# test on 3 samples
out = net.predict(x_test)
print("\n")
print("predicted values : ")
print(out, end="\n")
print("true values : ")
print(y_test[0:3])

epoch 1 35 error=28.424038
accuracy= 71.575962
epoch 2 35 error=28.424500
accuracy= 71.575500
epoch 3 35 error=28.424500
accuracy= 71.575500
epoch 4 35 error=28.424500
accuracy= 71.575500
epoch 5 35 error=28.424500
accuracy= 71.575500
epoch 6 35 error=28.424500
accuracy= 71.575500
epoch 7 35 error=28.424500
accuracy= 71.575500
epoch 8 35 error=28.424500
accuracy= 71.575500
epoch 9 35 error=28.424500
accuracy= 71.575500
epoch 10 35 error=28.424500
accuracy= 71.575500
epoch 11 35 error=28.424500
accuracy= 71.575500
epoch 12 35 error=28.424500
accuracy= 71.575500
epoch 13 35 error=28.424500
accuracy= 71.575500
epoch 14 35 error=28.424500
accuracy= 71.575500
epoch 15 35 error=28.424500
accuracy= 71.575500
epoch 16 35 error=28.424500
accuracy= 71.575500
epoch 17 35 error=28.424500
accuracy= 71.575500
epoch 18 35 error=28.424500
accuracy= 71.575500
epoch 19 35 error=28.424500
accuracy= 71.575500
epoch 20 35 error=28.424500
accuracy= 71.575500
epoch 21 35 error=28.424500
accuracy= 71.575500
e

In [34]:
net = Network()
net.add(FClayer(28*28, 100))              
net.add(ActivationLayer(tanh, tanh_prime))
net.add(FClayer(100, 50))                 
net.add(ActivationLayer(tanh, tanh_prime))
net.add(FClayer(50, 10))                  
net.add(ActivationLayer(tanh, tanh_prime))

In [35]:
net.use(mse, mse_prime)
net.fit(x_train[0:2000], y_train[0:2000], epochs= 35, learning_rate=0.05)

# test on 3 samples
out = net.predict(x_test)
print("\n")
print("predicted values : ")
print(out, end="\n")
print("true values : ")
print(y_test[0:3])

epoch 1 35 error=38.383917
accuracy= 61.616083
epoch 2 35 error=38.403041
accuracy= 61.596959
epoch 3 35 error=38.403235
accuracy= 61.596765
epoch 4 35 error=38.403313
accuracy= 61.596687
epoch 5 35 error=38.403356
accuracy= 61.596644
epoch 6 35 error=38.403383
accuracy= 61.596617
epoch 7 35 error=38.403401
accuracy= 61.596599
epoch 8 35 error=38.403415
accuracy= 61.596585
epoch 9 35 error=38.403425
accuracy= 61.596575
epoch 10 35 error=38.403433
accuracy= 61.596567
epoch 11 35 error=38.403440
accuracy= 61.596560
epoch 12 35 error=38.403445
accuracy= 61.596555
epoch 13 35 error=38.403450
accuracy= 61.596550
epoch 14 35 error=38.403453
accuracy= 61.596547
epoch 15 35 error=38.403457
accuracy= 61.596543
epoch 16 35 error=38.403460
accuracy= 61.596540
epoch 17 35 error=38.403462
accuracy= 61.596538
epoch 18 35 error=38.403464
accuracy= 61.596536
epoch 19 35 error=38.403466
accuracy= 61.596534
epoch 20 35 error=38.403468
accuracy= 61.596532
epoch 21 35 error=38.403470
accuracy= 61.596530
e

In [37]:
net = Network()
net.add(FClayer(28*28, 100))              
net.add(ActivationLayer(ReLU, ReLU_prime))
net.add(FClayer(100, 50))                 
net.add(ActivationLayer(ReLU, ReLU_prime))
net.add(FClayer(50, 10))                  
net.add(ActivationLayer(softmax, softmax_prime))

In [38]:
net.use(mse, mse_prime)
net.fit(x_train[0:2000], y_train[0:2000], epochs= 35, learning_rate=0.05)

# test on 3 samples
out = net.predict(x_test)
print("\n")
print("predicted values : ")
print(out, end="\n")
print("true values : ")
print(y_test[0:3])

epoch 1 35 error=27.624465
accuracy= 72.375535
epoch 2 35 error=27.626600
accuracy= 72.373400
epoch 3 35 error=27.626600
accuracy= 72.373400
epoch 4 35 error=27.626477
accuracy= 72.373523
epoch 5 35 error=27.626600
accuracy= 72.373400
epoch 6 35 error=27.626600
accuracy= 72.373400
epoch 7 35 error=27.626600
accuracy= 72.373400
epoch 8 35 error=27.626600
accuracy= 72.373400
epoch 9 35 error=27.626600
accuracy= 72.373400
epoch 10 35 error=27.626600
accuracy= 72.373400
epoch 11 35 error=27.626600
accuracy= 72.373400
epoch 12 35 error=27.626600
accuracy= 72.373400
epoch 13 35 error=27.626600
accuracy= 72.373400
epoch 14 35 error=27.626600
accuracy= 72.373400
epoch 15 35 error=27.626600
accuracy= 72.373400
epoch 16 35 error=27.626600
accuracy= 72.373400
epoch 17 35 error=27.626600
accuracy= 72.373400
epoch 18 35 error=27.626600
accuracy= 72.373400
epoch 19 35 error=27.626600
accuracy= 72.373400
epoch 20 35 error=27.626600
accuracy= 72.373400
epoch 21 35 error=27.626600
accuracy= 72.373400
e